<a href="https://colab.research.google.com/gist/anr2me/bf8f651b8c4a9294ce72237bf1127684/ovi-test.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>


Colab: Upload your input files from File Browser menu.

Kaggle: Upload your input files from File -> Upload Input -> Upload Data

In [ ]:


!uname -a
!free -h
!pwd
!pip install -U pip uv virtualenv GitPython loglevel
!git config --global core.fileMode
!git config --global pull.rebase true

import os
from datetime import datetime, timedelta
start_time = datetime.now()

!mkdir -p "/kaggle/working"
!mkdir -p "/kaggle/input"
!mkdir -p "/kaggle/temp"
!mkdir -p "/tmp/xdg_runtime"
!mkdir -p "/content"
current_dir = !pwd #["/content", "/kaggle/working","/kaggle/input","/kaggle/temp"]
WORKSPACE = "/content" # current_dir[0]
os.environ['WORKSPACE']=WORKSPACE
print(f"Workspace at {WORKSPACE}")
%cd "$WORKSPACE"

os.environ['XDG_RUNTIME_DIR']="/tmp/xdg_runtime"
os.environ['MPLBACKEND']="Agg"
#os.environ['PYTHONVERBOSE']="1"

# Create a bash script at /usr/bin/
shcontent = """
[ -f "$WORKSPACE/venv/bin/activate" ] && echo "Using VENV at $WORKSPACE" && source "$WORKSPACE/venv/bin/activate"; "$@"
"""
with open('/usr/bin/venv.sh', 'w') as file:
  file.write(shcontent)
!chmod +x /usr/bin/venv.sh

print("-= Creating/Restoring Virtual Environment =-")
![ ! -f "venv/bin/activate" ] && echo -= Initial Python Virtual Environment =- && virtualenv venv

print("-= Installing Default Dependencies =-")
!venv.sh pip install -U pip uv setuptools wheel ninja jedi loglevel einops
!venv.sh pip install torch==2.5.1 torchvision==0.20.1 torchaudio==2.5.1
#!venv.sh pip install -U torch torchao torchvision torchaudio xformers --index-url https://download.pytorch.org/whl/cu129
!venv.sh pip install triton sageattention #flash-attn-triton
!venv.sh pip install flash_attn --no-build-isolation

print("-= Installing Ovi repository =-")
![ ! -d Ovi ] && echo -= Initial setup Ovi =- && git clone --depth=1500 --branch main --single-branch https://github.com/character-ai/Ovi.git
%cd Ovi
!git pull
!venv.sh pip install -r requirements.txt # Using old numpy 1.26.4

print("-= Updating site-packages with VENV =-")
import sys
full_python_version = sys.version
python_version_number = ".".join(full_python_version.split(" ")[0].split(".")[:2])
print(f"Python Ver = {python_version_number}")
python_ver_num = python_version_number.replace(".","")

import torch
full_pytorch_version = torch.__version__
pytorch_version_number = ".".join(full_pytorch_version.split(" ")[0].split(".")[:2])
print(f"PyTorch Ver = {pytorch_version_number}")

print(f"Adding site-packages {WORKSPACE}/venv/lib/python{python_version_number}/site-packages")
import site
site.addsitedir(f"{WORKSPACE}/venv/lib/python{python_version_number}/site-packages")
sys.path.append(f"{WORKSPACE}/venv/bin")
sys.path.append(f"{WORKSPACE}/venv/lib/python{python_version_number}/site-packages")

print("-= Downloading Weights =-")
# Optional can specific --output-dir to download to a specific directory (default is ./ckpts)
# but if a custom directory is used, the inference yaml has to be updated with the custom directory
!venv.sh python3 download_weights.py --output-dir /kaggle/temp/ckpts

print("-= Configure Ovi =-")
# Uploaded Input files at'/kaggle/input' directory
# Downloadable Output files at '/kaggle/working' directory

config_content = """
# Output and Model Configuration
ckpt_dir: /kaggle/temp/ckpts #./ckpts
output_dir: /kaggle/working

# Generation Quality Settings
num_steps: 50
solver_name: unipc
shift: 5.0
seed: 103

# Guidance Strength Control
audio_guidance_scale: 3.0
video_guidance_scale: 4.0
slg_layer: 11

# Multi-GPU and Performance
sp_size: 1
cpu_offload: True

# Input Configuration
each_example_n_times: 1
mode: "t2v" # ["t2v", "i2v", "t2i2v"] all comes with audio
video_frame_height_width: [512, 992] # only useful if mode = t2v or t2i2v, recommended values: [512, 992], [992, 512], [960, 512], [512, 960], [720, 720], [448, 1120]
text_prompt: "a man proposing on one knee, while offering a large diamond ring to a grim reaper, as he says, <S>Will you marry me?<E>. After a brief pause, the grim reaper says, <S>You are courting death.<E><AUDCAP>A low-pitched male voice.<ENDAUDCAP>" #./example_prompts/gpt_examples_i2v.csv

# Quality Control (Negative Prompts)
video_negative_prompt: "jitter, bad hands, blur, distortion"  # Artifacts to avoid in video
audio_negative_prompt: "robotic, muffled, echo, distorted"    # Artifacts to avoid in audio
"""
with open("./ovi/configs/inference/inference_fusion.yaml", 'w') as file:
  file.write(config_content)

print("-= Running Inference =-")
start_time2 = datetime.now()
#!venv.sh python3 inference.py --config-file "./ovi/configs/inference/inference_fusion.yaml"
#!venv.sh torchrun --nnodes 1 --nproc_per_node 4 inference.py --config-file "./ovi/configs/inference/inference_fusion.yaml"
!venv.sh python3 gradio_app.py --cpu_offload

time_delta2 = datetime.now() - start_time2
print(f"-= Inference Done! ({str(timedelta(seconds=time_delta2.total_seconds()))}) =-")

time_delta = datetime.now() - start_time
print(f"-= All Done! ({str(timedelta(seconds=time_delta.total_seconds()))}) =-")

Linux 98afc3a498e5 6.6.97+ #1 SMP PREEMPT_DYNAMIC Sat Sep  6 09:54:41 UTC 2025 x86_64 x86_64 x86_64 GNU/Linux
               total        used        free      shared  buff/cache   available
Mem:            12Gi       721Mi       8.8Gi       1.0Mi       3.1Gi        11Gi
Swap:             0B          0B          0B
/content
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 22.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.2/21.2 MB 124.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.0/6.0 MB 141.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 469.0/469.0 kB 42.3 MB/s eta 0:00:00
  Attempting uninstall: pip
    Found existing installation: pip 24.1.2
    Uninstalling pip-24.1.2:
      Successfully uninstalled pip-24.1.2
Workspace at /content
-= Creating/Restoring Virtual Environment =-
-= Initial Python Virtual Environment =-
created virtual environment CPython3.12.11.final.0-64 in 318ms
  creator CPython3Posix(dest=/content/venv, 